In [1]:
%reload_ext autoreload
%autoreload 2
# %matplotlib widget

In [2]:
import rioxarray
import satio_pc
from satio_pc import parallelize

from satio_pc.grid import get_blocks_gdf
from satio_pc.sentinel2 import load_sentinel2_tile, preprocess_s2
from satio_pc.preprocessing.clouds import scl_to_mask


def ram_usage():
    import psutil
    # Getting % usage of virtual_memory ( 3rd field)
    print('RAM memory % used:', psutil.virtual_memory()[2])
    # Getting usage of virtual_memory in GB ( 4th field)
    print('RAM Used (GB):', psutil.virtual_memory()[3]/1000000000)
    

# worldcover settings
settings = {
    
    "l2a": {
        "composite": {"freq": 10, "window": 20},
        "mask": {"erode_r": 3,
                 "dilate_r": 13,
                 "mask_values": [1, 3, 8, 9, 10, 11],
                 "max_invalid_ratio": 1}},
}



# with open('../../sastoken') as f:
#     sas_token = f.read()
    
# container_client = azure.storage.blob.ContainerClient(
#     "https://dza2.blob.core.windows.net",
#     container_name="feats",
#     credential=sas_token,
# ) 

In [4]:
from satio_pc.indices import get_rsi_function, RSI_META_S2

In [10]:
name = 'auc'

f = get_rsi_function(name)

NameError: name 'function_name' is not defined

In [6]:
f

<function satio_pc.indices.norm_diff(arr1, arr2)>

In [5]:
s2.ndvi.bands

('B08', 'B04')

In [11]:
import numpy as np

1 < np.inf

True

In [3]:
ram_usage()

RAM memory % used: 4.9
RAM Used (GB): 2.565881856


In [17]:
s2.__getattribute__('auc').bands

('B02', 'B03', 'B04', 'B08', 'B11', 'B12')

In [30]:
dsm

<xarray.DataArray 'setitem-41259d72bf5b69c45d69f33e35ae3443' (time: 37,
                                                              band: 11,
                                                              y: 1024, x: 1024)>
dask.array<xarray-<this-array>, shape=(37, 11, 1024, 1024), dtype=float32, chunksize=(37, 11, 256, 256), chunktype=numpy.ndarray>
Coordinates:
  * time     (time) datetime64[ns] 2022-01-06 2022-01-16 ... 2023-01-01
  * band     (band) object 'B02' 'B03' 'B04' 'B08' ... 'B8A' 'B09' 'B11' 'B12'
  * y        (y) float64 5.7e+06 5.7e+06 5.7e+06 ... 5.69e+06 5.69e+06 5.69e+06
  * x        (x) float64 6e+05 6e+05 6e+05 ... 6.102e+05 6.102e+05 6.102e+05
Attributes:
    bounds:   (600000.0, 5689760.0, 610240.0, 5700000.0)

In [34]:
dsm[0, 0, :10, :10].compute()

<xarray.DataArray 'setitem-41259d72bf5b69c45d69f33e35ae3443' (y: 10, x: 10)>
array([[0.0641, 0.0637, 0.0652, 0.0679, 0.0643, 0.0659, 0.0708, 0.0717,
        0.0563, 0.042 ],
       [0.0625, 0.062 , 0.0638, 0.0651, 0.0581, 0.058 , 0.0587, 0.0604,
        0.0508, 0.0398],
       [0.0589, 0.0556, 0.0553, 0.0567, 0.0486, 0.0448, 0.045 , 0.0487,
        0.0454, 0.0398],
       [0.0572, 0.0534, 0.0521, 0.052 , 0.0425, 0.0376, 0.0398, 0.0377,
        0.0347, 0.0357],
       [0.0533, 0.0496, 0.0487, 0.0467, 0.0367, 0.0344, 0.0368, 0.0364,
        0.0337, 0.0346],
       [0.0492, 0.045 , 0.0443, 0.0412, 0.035 , 0.0361, 0.0365, 0.0346,
        0.0335, 0.0345],
       [0.0478, 0.043 , 0.0369, 0.0357, 0.0359, 0.0367, 0.035 , 0.0341,
        0.0328, 0.0335],
       [0.0429, 0.0437, 0.0378, 0.0355, 0.0374, 0.0337, 0.0309, 0.0317,
        0.0311, 0.0294],
       [0.0397, 0.0396, 0.0352, 0.0343, 0.0355, 0.031 , 0.0309, 0.0312,
        0.0294, 0.0276],
       [0.0366, 0.0377, 0.0346, 0.0342, 0.0344, 0.0299, 0.0312, 0.0316,
        0.0302, 0.0301]], dtype=float32)
Coordinates:
    time     datetime64[ns] 2022-01-06
    band     <U3 'B02'
  * y        (y) float64 5.7e+06 5.7e+06 5.7e+06 ... 5.7e+06 5.7e+06 5.7e+06
  * x        (x) float64 6e+05 6e+05 6e+05 ... 6.001e+05 6.001e+05 6.001e+05
Attributes:
    bounds:   (600000.0, 5689760.0, 610240.0, 5700000.0)

In [18]:
# load tile data

year = 2022
tile_id = '31UFS'

start_date = f'{year}-01-01'
end_date = f'{year + 1}-01-01'

max_cloud_cover = 90

ds10, ds20, ds60, scl = load_sentinel2_tile(tile_id,
                                            start_date,
                                            end_date,
                                            max_cloud_cover)

In [19]:
# set up mask preprocessing

scl_settings = settings['l2a']['mask']

keys = "erode_r, dilate_r, max_invalid_ratio, mask_values".split(', ')
erode_r, dilate_r, max_invalid_ratio, mask_values = [scl_settings[k]
                                                     for k in keys]

scl_post = scl_to_mask(scl,
                       mask_values=mask_values,
                       erode_r=erode_r,
                       dilate_r=dilate_r,
                       max_invalid_ratio=max_invalid_ratio)
scl20 = scl_post.mask

### Block processing 

In [20]:
# select block
blocks_gdf = get_blocks_gdf([tile_id])
block = blocks_gdf.iloc[0]
block

tile                                                    31UFS
bounds                     (600000, 5689760, 610240, 5700000)
geometry    POLYGON ((4.435991332247422 51.35030439069133,...
area                                              104857600.0
epsg                                                    32631
block_id                                                    0
Name: 0, dtype: object

In [21]:
# clip tile dataarrays to block aoi
ds10_block = ds10.rio.clip_box(*block.bounds).satio.harmonize()
ds20_block = ds20.rio.clip_box(*block.bounds).satio.harmonize()
scl20_block = scl20.rio.clip_box(*block.bounds)

In [22]:
comp_settings = settings['l2a']['composite']

dsm = preprocess_s2(ds10_block,
                    ds20_block,
                    scl20_block,
                    start_date, end_date,
                    composite_freq=comp_settings['freq'],
                    composite_window=comp_settings['window'])

2023-03-15 10:31:20.752 | INFO     | satio_pc.sentinel2:preprocess_s2:280 - Loading block data
2023-03-15 10:32:28.837 | INFO     | satio_pc.sentinel2:preprocess_s2:298 - Compositing 10m block data
2023-03-15 10:33:20.660 | INFO     | satio_pc.sentinel2:preprocess_s2:307 - Interpolating 10m block data
2023-03-15 10:33:35.646 | INFO     | satio_pc.sentinel2:preprocess_s2:320 - Compositing 20m block data
2023-03-15 10:34:00.645 | INFO     | satio_pc.sentinel2:preprocess_s2:329 - Interpolating 20m block data
2023-03-15 10:34:04.944 | INFO     | satio_pc.sentinel2:preprocess_s2:336 - Merging 10m and 20m series
2023-03-15 10:34:04.959 | INFO     | satio_pc.preprocessing.timer:log:57 - 10m loading took 0.31 minutes
2023-03-15 10:34:04.960 | INFO     | satio_pc.preprocessing.timer:log:57 - 10m compositing took 1.02 minutes
2023-03-15 10:34:04.961 | INFO     | satio_pc.preprocessing.timer:log:57 - 10m interpolation took 0.20 minutes
2023-03-15 10:34:04.962 | INFO     | satio_pc.preprocessing.t

In [26]:
ram_usage()

RAM memory % used: 6.1
RAM Used (GB): 3.353522176


In [24]:
dsm

<xarray.DataArray 'setitem-41259d72bf5b69c45d69f33e35ae3443' (time: 37,
                                                              band: 11,
                                                              y: 1024, x: 1024)>
dask.array<xarray-<this-array>, shape=(37, 11, 1024, 1024), dtype=float32, chunksize=(37, 11, 256, 256), chunktype=numpy.ndarray>
Coordinates:
  * time     (time) datetime64[ns] 2022-01-06 2022-01-16 ... 2023-01-01
  * band     (band) object 'B02' 'B03' 'B04' 'B08' ... 'B8A' 'B09' 'B11' 'B12'
  * y        (y) float64 5.7e+06 5.7e+06 5.7e+06 ... 5.69e+06 5.69e+06 5.69e+06
  * x        (x) float64 6e+05 6e+05 6e+05 ... 6.102e+05 6.102e+05 6.102e+05
Attributes:
    bounds:   [ 600000. 5689760.  610240. 5700000.]

In [29]:
dsm.satio.rgb(vmax=0.2)

In [18]:
import numpy as np

In [26]:
p = np.percentile(dsm, [10, 25, 50, 75, 90], axis=0)

In [27]:
p.shape

(5, 11, 1024, 1024)

In [25]:
ram_usage()

RAM memory % used: 8.5
RAM Used (GB): 5.018755072


In [ ]:
# compute the indices from list and cache them
# compute percentiles and cache on bands and indices
# merge percentiles 


# indices should be collected as a list
# map_blocks -> load block -> compute all indices on block


# class Car:
#     def __init__(self, make, model):
#         self.make = make
#         self.model = model

#     def __getattr__(self, attr):
#         if attr == 'start':
#             # Define the default behavior for the start method
#             def start_default():
#                 print(f'Starting the {self.make} {self.model}...')
#                 return 'Vroom!'
            
#             # Only return the default behavior if the attribute doesn't exist
#             if not hasattr(self, attr):
#                 return start_default
                
#         # Raise an AttributeError for any other attribute or method
#         raise AttributeError(f"'{type(self).__name__}' object has no attribute '{attr}'")

# define satio indices object. when calling an index, we can compute it using the meta dict by checking band names and running the function by
# mapping it to the blocks

# if you have multiple indices, we can apply a series of functions to the bands